In [17]:
from pinecone import Pinecone, ServerlessSpec
import boto3
import json

pc = Pinecone(api_key="pcsk_7JLSus_U3m4SxY6snjBuCB5KAqBXGMm2h5YrZkSicYdCqQhVwDCNVGrybyf26H8MQVDwTa")

In [5]:
# Create index if not exists
index_name = "user-posts-with-url"
if index_name not in pc.list_indexes():
    pc.create_index(
        name=index_name,
        dimension=1024,  # Match Bedrock embedding dimensions
        metric="cosine",
        spec=ServerlessSpec(
        cloud="aws",
        region="us-east-1"
    ) 
    )
pinecone_index = pc.Index(index_name)

In [16]:
pc = Pinecone(api_key="pcsk_7JLSus_U3m4SxY6snjBuCB5KAqBXGMm2h5YrZkSicYdCqQhVwDCNVGrybyf26H8MQVDwTa")
pinecone_index = pc.Index("user-posts-with-url")
session = boto3.Session(region_name="us-east-1")
s3 = boto3.client('s3')
bedrock = boto3.client('bedrock-runtime', region_name='us-east-1')

In [11]:
import pandas as pd
from datetime import datetime, timedelta
from dateutil.relativedelta import relativedelta

In [9]:
df = pd.read_csv('linkedin_posts.csv')

In [19]:
today = pd.Timestamp("today").normalize()          # → 2025-05-01 in this session

def to_date(relative: str, anchor=today):
    """Convert strings like '3mo', '2w', '1d', '1yr' into a concrete date."""
    if relative.endswith("d"):
        return anchor - timedelta(days=int(relative[:-1]))
    if relative.endswith("w"):
        return anchor - timedelta(weeks=int(relative[:-1]))
    if relative.endswith("mo"):
        return anchor - relativedelta(months=int(relative[:-2]))
    if relative.endswith("yr"):
        return anchor - relativedelta(years=int(relative[:-2]))
    raise ValueError(f"Unrecognised offset: {relative}")

df["post_date"] = df["post_timestamp"].apply(to_date).astype(str)

In [20]:
df

post_content  \
0    Dear International Students,\nNo Summer Intern...   
1    I received 4 Research Assistant offers during ...   
2    AI world was buzzing this week! Here's your qu...   
3    Dear International Students,\nNo Summer Intern...   
4    Dear International Students,\nNo Summer Intern...   
..                                                 ...   
97   This is the only SQL cheat sheet you need!\n\n...   
98   2021: The Year of Post-Covid Market\n2023: The...   
99   That moment when you realize AI can do your jo...   
100  What if people on LinkedIn were honest?!\n\nI'...   
101  My LinkedIn profile says I’m working as a Data...   

                                              post_url post_timestamp  \
0    https://www.linkedin.com/feed/update/urn:li:ac...             3d   
1    https://www.linkedin.com/feed/update/urn:li:ac...             4d   
2    https://www.linkedin.com/feed/update/urn:li:ac...             5d   
3    https://www.linkedin.com/feed/update/urn:li:ac...             1w   
4    https://www.linkedin.com/feed/update/urn:li:ac...             1w   
..                                                 ...            ...   
97   https://www.linkedin.com/feed/update/urn:li:ac...            3mo   
98   https://www.linkedin.com/feed/update/urn:li:ac...            3mo   
99   https://www.linkedin.com/feed/update/urn:li:ac...            3mo   
100  https://www.linkedin.com/feed/update/urn:li:ac...            3mo   
101  https://www.linkedin.com/feed/update/urn:li:ac...            3mo   

      post_date  
0    2025-04-28  
1    2025-04-27  
2    2025-04-26  
3    2025-04-24  
4    2025-04-24  
..          ...  
97   2025-02-01  
98   2025-02-01  
99   2025-02-01  
100  2025-02-01  
101  2025-02-01  

[102 rows x 4 columns]

In [22]:
user_email = 'hpprasad2000@gmail.com'
vectors = []
for i, row in df.iterrows():
    response = bedrock.invoke_model(
        body=json.dumps({"inputText": row['post_content']}),
        modelId="amazon.titan-embed-text-v2:0",
        accept="application/json"
    )
    embedding = json.loads(response['body'].read())['embedding']
    
    vectors.append({
        "id": f"{user_email}-{hash(row['post_content'])}",
        "values": embedding,
        "metadata": {
            "user_email": user_email,
            "text": row['post_content'],
            # "source": f"s3://{BUCKET_NAME}/{s3_key}",
            "post_url": row['post_url'],
            "post_date": row['post_date']
        }
    })

# 4. Store in Pinecone
if vectors:
    print(vectors)
    pinecone_index.upsert(vectors=vectors)

[{'id': 'hpprasad2000@gmail.com-8267861990464864880', 'values': [-0.024917354807257652, 0.0743863582611084, -0.04672469571232796, -0.013356017880141735, 0.0519547238945961, -0.022245286032557487, -0.040162086486816406, -0.026395954191684723, -0.03556033596396446, -0.012617236003279686, 0.05777277052402496, 0.05491385981440544, -0.01871454156935215, 0.01785627007484436, 0.038639191538095474, -0.007809676695615053, -0.04130679741501808, 0.0069768307730555534, 0.04935663565993309, -0.029645415022969246, 0.07396119087934494, 0.0431596040725708, -0.02528989501297474, 0.03999416157603264, 0.010400213301181793, -0.06594496965408325, 0.005690347868949175, 0.026704950258135796, 0.026680873706936836, -0.022060595452785492, 0.07314998656511307, 0.06171650066971779, -0.02518077753484249, -0.011245192028582096, 0.013731032609939575, 0.061588771641254425, 0.0009909260552376509, 0.019893012940883636, -0.028897857293486595, -0.05491047725081444, 0.008034654892981052, 0.011872930452227592, -0.002987045

In [23]:
vectors

[{'id': 'hpprasad2000@gmail.com-8267861990464864880',
  'values': [-0.024917354807257652,
   0.0743863582611084,
   -0.04672469571232796,
   -0.013356017880141735,
   0.0519547238945961,
   -0.022245286032557487,
   -0.040162086486816406,
   -0.026395954191684723,
   -0.03556033596396446,
   -0.012617236003279686,
   0.05777277052402496,
   0.05491385981440544,
   -0.01871454156935215,
   0.01785627007484436,
   0.038639191538095474,
   -0.007809676695615053,
   -0.04130679741501808,
   0.0069768307730555534,
   0.04935663565993309,
   -0.029645415022969246,
   0.07396119087934494,
   0.0431596040725708,
   -0.02528989501297474,
   0.03999416157603264,
   0.010400213301181793,
   -0.06594496965408325,
   0.005690347868949175,
   0.026704950258135796,
   0.026680873706936836,
   -0.022060595452785492,
   0.07314998656511307,
   0.06171650066971779,
   -0.02518077753484249,
   -0.011245192028582096,
   0.013731032609939575,
   0.061588771641254425,
   0.0009909260552376509,
   0.01989301